### Exercise 39

#### Import

In [1]:
import numpy as np
from numpy.linalg import inv, det
from numpy.linalg import inv
from scipy.linalg import lu_solve
import pandas as pd
import matplotlib.pyplot as plt

#### Data

In [2]:
df = pd.read_csv('sinusoidal.csv')

x = df[['x']].to_numpy()
y = df[['y']].to_numpy()
n = len(x)

x = x.reshape((n,))
y = y.reshape((n,))

#### Functions

In [3]:
def create_Phi_poly(x, p, n):
    X = np.zeros((n, p))
    
    for i in range(n):
        for j in range(p):
            X[i][j] = x[i]**j
    return X


def create_Phi_gauss(x, p, n):
    X = np.zeros((n, p))
    centres = np.linspace(0, 1, p)
    
    for i in range(n):
        for j in range(p):
            X[i][j] = np.exp(-50*(x[i] - centres[j])**2)
    return X


def fitted_curve_poly(space, w, mplot, p):
    result = np.zeros(mplot)
    for j in range(p):
        result += w[j] * space**j
    return result


def fitted_curve_gauss(space, w, mplot, p):
    result = np.zeros(mplot)
    centres = np.linspace(0, 1, p)
    for j in range(p):
        result += w[j] * np.exp(-50*(space - centres[j])**2)
    return result


def get_log_ML(alpha, beta, x, y, n, p):
    Phi = create_Phi_poly(x, p, n)
    A = alpha*np.eye(p) + beta*Phi.T @ Phi
    detA = det(A)
    S = inv(A)
    m = beta*S @ Phi.T @ y
    Em = .5*beta*(y - Phi @ m).T @ (y - Phi @ m) + .5*alpha* m.T @ m
    return (p/2)*np.log(alpha) + (n/2)*np.log(beta) - Em - (1/2)*np.log(detA) - (n/2)*np.log(2*np.pi)

#### Parameters

In [4]:
p = 4
alpha = 0
beta = 1
counter = 0

old_alpha = -np.inf
old_beta = -np.inf
tolerance = 1e-20

In [5]:
# Phi and the eigenvalues of Phi.T @ Phi
Phi = create_Phi_poly(x, p, n)
eigenvals, eigenvecs = np.linalg.eigh(Phi.T @ Phi)

In [6]:
# Posterior parameters
A = alpha*np.eye(p) + beta*Phi.T @ Phi
detA = det(A)
S = inv(A)
m = beta*S @ Phi.T @ y

In [7]:
while True:
    # Update alpha and beta
    lambdas = beta * eigenvals
    gamma = np.sum(lambdas/(alpha + lambdas))
    alpha = gamma/(m.T @ m)
    betainv = 0
    for i in range(n):
        betainv += (y[i] - m.T @ Phi[i])**2
    betainv *= 1/(n - gamma)
    beta = betainv**(-1)
    #beta = (1/(n - gamma) * (y - Phi @ m).T @ (y - Phi @ m))**(-1)
    
    # Update posterior parameters accordingly
    A = alpha*np.eye(p) + beta*Phi.T @ Phi
    detA = det(A)
    S = inv(A)
    m = beta*S @ Phi.T @ y
    
    # Evaluate new marginal likelihood
    Em = .5*beta*(y - Phi @ m).T @ (y - Phi @ m) + .5*alpha*(m.T @ m)
    log_ML = .5*p*np.log(alpha) + .5*n*np.log(beta) - Em - .5*np.log(detA) - .5*n*np.log(2*np.pi)
    
    # Stop if convergence achieved
    if (alpha - old_alpha)**2 + (beta - old_beta)**2 < tolerance:
        break
    
    old_alpha = alpha
    old_beta = beta
    counter += 1

In [8]:
print(f'alpha = {np.round(alpha, 4)}')
print(f'beta = {np.round(beta, 4)}')
print(f'log ML = {np.round(get_log_ML(alpha, beta, x, y, n, p), 4)}')

alpha = 0.0032
beta = 31.4231
gamma (effective number of parameters) = 3.9604
log ML = -10.7449


### Exercise 40

In [9]:
print(f'gamma (effective number of parameters) = {np.round(gamma, 4)}')

gamma (effective number of parameters) = 3.9604
